In [223]:
import matplotlib.pyplot as plt
import matplotlib.cm as cm
import networkx as nx
import csv

hist = []
files = ['../excel/dados_historicos_alunos_de_EngComputacaoCuritiba formados.csv',
         '../excel/dados_historicos_alunos_de_EngComputacaoCuritiba regulares.csv',
         '../excel/dados_historicos_alunos_de_EngComputacaoCuritiba trancados.csv',
         '../excel/dados_historicos_alunos_de_EngComputacaoCuritiba desistentes mudancas curso.csv'
         ]

# preenche as listas iniciais
for file in files:
    print(file)
    with open(file, 'r') as csvfile:   
        reader = csv.DictReader(csvfile, delimiter=';')
        for row in reader:
            hist.append(row)
print(len(hist))
print(hist[0])

../excel/dados_historicos_alunos_de_EngComputacaoCuritiba formados.csv
../excel/dados_historicos_alunos_de_EngComputacaoCuritiba regulares.csv
../excel/dados_historicos_alunos_de_EngComputacaoCuritiba trancados.csv
../excel/dados_historicos_alunos_de_EngComputacaoCuritiba desistentes mudancas curso.csv
76844
{'ID_ANONIMO': '13236', 'CR': '0,6826', 'PERIODO': '1', 'INGRESSO': '12/07/07', 'CODIGO': 'IF68E', 'ANO': '2012', 'NOTA': '8,2', 'CH': '60', 'SITUACAOALUNO': 'Formado'}


In [224]:
# função para verificar se um aluno teve seu ingresso antes ou depois de 2014
def beforeClasses(date):
    year = date.split('/')[2]
    if (int(year) < 14):
        return True
    return False

In [225]:
# Remove todos os alunos que ingressaram antes de 2014 
for i in range(len(hist)):
    if (i == len(hist)):
        break
    if (beforeClasses(hist[i]['INGRESSO'].split(" ")[0])):
        hist.pop(i)
        i = 0

# Remove todos dados de reprovações (matérias repetidas)
for i in range(len(hist)):
    for j in range(i, len(hist)):
        if (j == len(hist)):
            break
        if (hist[i]["ID_ANONIMO"] != hist[j]["ID_ANONIMO"]):
            break
        if (j < len(hist) and (i != j and (hist[i]["ID_ANONIMO"] == hist[j]["ID_ANONIMO"] and hist[i]["CODIGO"] == hist[j]["CODIGO"]))):
            hist.pop(j)
            j -= 5
len(hist)

# TODO: caso o aluno tenha reprovado em uma matéria, deve ser removido também. 
# Uma reprovação não conta para o sistema de recomendação

49188

In [226]:
G = nx.Graph()

# Adiciona todos os nós, que são os alunos
# Sem colocar nenhum aluno pré-2014
for line in hist:
    if (not beforeClasses(line['INGRESSO'].split(" ")[0])):
        if not G.has_node(line["ID_ANONIMO"]):
            G.add_node(line["ID_ANONIMO"])
G.nodes()

NodeView(('90729', '113853', '118844', '123664', '123676', '123677', '123686', '123688', '123736', '129034', '131006', '131014', '136341', '136730', '136731', '136736', '145077', '150873', '150878', '150887', '150892', '151217', '156158', '158257', '159067', '160836', '160839', '160852', '160855', '161216', '161223', '161226', '161228', '165431', '165432', '165685', '165892', '165894', '165895', '166050', '169043', '171740', '171745', '171746', '171749', '171750', '171751', '171754', '171755', '172044', '172045', '172046', '172207', '172208', '172248', '172307', '172974', '175962', '179385', '179393', '179397', '179408', '179624', '179652', '179819', '179822', '179823', '179944', '180984', '182856', '182913', '183413', '183414', '186021', '186024', '186036', '189048', '190493', '190494', '190495', '190499', '190508', '190615', '191284', '198372', '198543', '202261', '11357', '104342', '104372', '104768', '110307', '113861', '118817', '123657', '123682', '124800', '126813', '130359', '1

In [227]:
print(G.number_of_nodes())

901


In [228]:
# Verifica quais são as matérias obrigatórias, que não serão levadas em conta
optional = []
with open('../texts/optativas.txt', 'r') as f:   
    lines = f.readlines()
    for l in lines:
        optional.append(l.split(" ")[0])

print(optional)

['CSH30', 'CSV30', 'CSH42', 'CSI53', 'CSV40', 'CSR44', 'CSR41', 'CSR42', 'MA70C', 'CSB51', 'ED70T', 'CSB41', 'CSI41', 'DI84D', 'CSV45', 'CSR43', 'CSM44', 'CSM41', 'CSM43', 'ES70J', 'ES70B', 'CSM40', 'CSB53', 'ES70N', 'GE70F', 'CSA44', 'CSB54', 'CSH44', 'EEY41', 'ED70U', 'CSH43', 'CSE40', 'CSM30', 'CSI56', 'CSA45', 'FI70B', 'FI70D', 'CSA42', 'EL64B', 'CSV52', 'CSB52', 'CSD41', 'FI70A', 'CSD40', 'CSR53', 'CSG42', 'CSI58', 'CSI57', 'CSG48', 'CSV41', 'CSI51', 'CSW45', 'CSE43', 'CSI55', 'FCH7HB', 'CSR47', 'EEY44', 'CSH45', 'CSA41', 'EEC41', 'EL6CB', 'EEY43', 'CSR48', 'EEY42', 'EL6AE', 'CSH41', 'CSD52', 'EEY51', 'EEL51', 'CSI54', 'CSA43', 'CSW47', 'CSI31', 'IF6BV', 'CSR45', 'CSG44', 'FI70E', 'EL75H']


In [246]:
# Adiciona as arestas
with open('all_edges.txt', 'w') as f:
    for i in range(len(hist)):
        # o estudante deve estar no grafo
        if G.has_node(hist[i]["ID_ANONIMO"]):
            # a disciplina não pode ser obrigatória
            if (hist[i]["CODIGO"] in optional):
                for j in range(i, len(hist)):
                    # o estudante deve estar no grafo
                    if G.has_node(hist[j]["ID_ANONIMO"]):
                        # a disciplina não pode ser obrigatória
                        if (hist[j]["CODIGO"] in optional):
                            # os alunos deve ser diferentes
                            if (hist[i]["ID_ANONIMO"] != hist[j]["ID_ANONIMO"]):
                                # as disciplinas que eram obrigatorias antes de 2017 n contam
                                if (line['CODIGO'] != 'ES70N' or int(line['ANO']) > 2017):
                                    if (line['CODIGO'] != 'FI70D' or int(line['ANO']) > 2017):
                                       if (line['CODIGO'] != 'FI70A' or int(line['ANO']) > 2017) and \
                                           (line['CODIGO'] != 'GE70F' or int(line['ANO']) > 2017):
                                            # as matérias devem ser as mesmas
                                            if (hist[i]["CODIGO"] == hist[j]["CODIGO"]):
                                                f.write(hist[i]["ID_ANONIMO"] + " - " + hist[j]["ID_ANONIMO"] + " : " + hist[j]["CODIGO"] + "\n")
                                                if (G.has_edge(hist[i]["ID_ANONIMO"], hist[j]["ID_ANONIMO"])):
                                                    G[hist[i]["ID_ANONIMO"]][hist[j]["ID_ANONIMO"]]['weight'] += 1
                                                else:
                                                    G.add_edge(hist[i]["ID_ANONIMO"], hist[j]["ID_ANONIMO"], weight = 1) 

In [247]:
# Remover as arestas com peso pequeno
edges_remove = []
for u, v, a in G.edges(data=True):
    if a["weight"] < 0:
        edges_remove.append([u, v])
G.remove_edges_from(edges_remove)

In [248]:
print(G.number_of_edges())

17852


In [249]:
# ordena os vértices por grau, para verificar os alunos com maior n de matérias em comum
degrees = sorted(G.degree, key=lambda x: x[1], reverse=True)
remove = [node for node, degree in dict(G.degree()).items() if degree == 0]
G.remove_nodes_from(remove)
G.number_of_nodes()

260

In [250]:
with open('node_degree_all.txt', 'w') as f:
    for degree in degrees:
        f.write(str(degree) + "\n")

In [251]:
# Escreve o arquivo gexf para visualização de grafos
nx.write_gexf(G, "grafo_caminho.gexf")

In [252]:
# ordena as arestas por peso, buscando assim quais os estudantes mais relacionadas
edges = sorted(G.edges(data=True), key=lambda edge: edge[2].get('weight', 1))
with open('edge_weights.txt', 'w') as f1:
    for edge in edges:
        f1.write(str(edge) + "\n")


In [253]:
import leidenalg as la
import igraph as ig
# Separa o grafo em comunidades
# O alg usado para isso é o Leinden, com a biblioteca LeidenAlg
# para isso, é preciso transformar o grafo do networkX para Igraph
H = ig.Graph.from_networkx(G)
H.is_weighted()

True

In [254]:
ws = []
for e in H.es():
  ws.append(e['weight'])

In [255]:
ig.plot(H)

In [256]:
# Agora roda a partição
partition = la.find_partition(H, la.ModularityVertexPartition, weights=H.es()[:]["weight"], n_iterations=50)
ig.plot(partition)

In [257]:
partition.membership

[0,
 0,
 1,
 0,
 1,
 1,
 1,
 1,
 0,
 0,
 1,
 1,
 1,
 1,
 1,
 1,
 1,
 1,
 2,
 1,
 2,
 0,
 2,
 0,
 0,
 0,
 0,
 0,
 0,
 0,
 0,
 0,
 2,
 0,
 0,
 0,
 0,
 0,
 0,
 0,
 1,
 2,
 0,
 1,
 0,
 1,
 1,
 2,
 1,
 0,
 0,
 2,
 0,
 1,
 2,
 0,
 1,
 2,
 2,
 2,
 2,
 1,
 1,
 1,
 1,
 1,
 2,
 0,
 2,
 1,
 2,
 2,
 1,
 1,
 1,
 1,
 1,
 1,
 2,
 1,
 2,
 1,
 1,
 2,
 2,
 2,
 1,
 0,
 2,
 0,
 0,
 0,
 1,
 2,
 0,
 2,
 2,
 2,
 2,
 1,
 0,
 0,
 2,
 2,
 0,
 0,
 0,
 2,
 2,
 0,
 1,
 0,
 2,
 1,
 1,
 1,
 1,
 1,
 2,
 1,
 2,
 0,
 2,
 1,
 1,
 1,
 2,
 2,
 2,
 2,
 1,
 2,
 1,
 2,
 1,
 1,
 1,
 0,
 1,
 1,
 2,
 1,
 2,
 1,
 2,
 0,
 1,
 1,
 1,
 1,
 1,
 1,
 1,
 2,
 1,
 1,
 1,
 1,
 2,
 1,
 1,
 1,
 1,
 1,
 1,
 1,
 2,
 2,
 1,
 0,
 2,
 1,
 2,
 0,
 2,
 0,
 0,
 0,
 0,
 0,
 0,
 1,
 0,
 0,
 1,
 1,
 0,
 0,
 0,
 0,
 2,
 0,
 2,
 0,
 0,
 1,
 0,
 2,
 1,
 1,
 0,
 0,
 0,
 0,
 0,
 2,
 0,
 0,
 2,
 0,
 2,
 0,
 2,
 0,
 0,
 2,
 1,
 0,
 0,
 2,
 0,
 0,
 2,
 0,
 2,
 2,
 0,
 0,
 2,
 1,
 2,
 2,
 2,
 2,
 1,
 2,
 0,
 0,
 0,
 0,
 2,
 0,
 0,
 0,
 2,
 0,
 0,
 2,
 2,
 1,


In [258]:
com_0 = [H.vs()[idx]["_nx_name"] for idx, com in enumerate(partition.membership) if com == 0]
com_1 = [H.vs()[idx]["_nx_name"] for idx, com in enumerate(partition.membership) if com == 1]
com_2 = [H.vs()[idx]["_nx_name"] for idx, com in enumerate(partition.membership) if com == 2]
com_3 = [H.vs()[idx]["_nx_name"] for idx, com in enumerate(partition.membership) if com == 3]

comunidades = []
for y in range(0,3):
    comunidades.append([H.vs()[idx]["_nx_name"] for idx, com in enumerate(partition.membership) if com == y])

print(comunidades)

[['90729', '113853', '123664', '123736', '129034', '151217', '158257', '159067', '160836', '160839', '160852', '160855', '161216', '161223', '161226', '165431', '165432', '165685', '165892', '165894', '165895', '166050', '171745', '171749', '172044', '172045', '172207', '172307', '179944', '11357', '104768', '110307', '118817', '126813', '147820', '155125', '160837', '160841', '160846', '165898', '168864', '177170', '190684', '198761', '212903', '224204', '250128', '250152', '251697', '253829', '253830', '88453', '161840', '186224', '219036', '51969', '90293', '90327', '119255', '125585', '125626', '131755', '145760', '152094', '153843', '156565', '157889', '160835', '160838', '160847', '160851', '161072', '161103', '161222', '161532', '161839', '165430', '165682', '165687', '165689', '171753', '171897', '172038', '172041', '172306', '172409', '172973', '177424', '185556', '202690', '202703', '241309', '250148'], ['118844', '123676', '123677', '123686', '123688', '131006', '131014', '1

In [259]:
# Pandas
import pandas as pd
# preenche as listas iniciais
dados = []
for file in files:
    print(file)
    with open(file, 'r') as csvfile:   
        dados.append(pd.read_csv(csvfile, delimiter=';'))

dados = pd.concat(dados)

../excel/dados_historicos_alunos_de_EngComputacaoCuritiba formados.csv
../excel/dados_historicos_alunos_de_EngComputacaoCuritiba regulares.csv
../excel/dados_historicos_alunos_de_EngComputacaoCuritiba trancados.csv
../excel/dados_historicos_alunos_de_EngComputacaoCuritiba desistentes mudancas curso.csv


In [273]:
dados_filtrados = dados[dados.CODIGO.apply(lambda a: a in optional)]
dados_filtrados = dados_filtrados[[int(x[3].split('/')[2].split(' ')[0]) >= 14 for x in dados_filtrados.values]]
dados_filtrados = dados_filtrados[[float(str(x[7]).replace(',','.')) >= 6 for x in dados_filtrados.values]]
dados_filtrados = dados_filtrados[[x[4] != 'ES70N' or x[5] > 2017 for x in dados_filtrados.values]]
dados_filtrados = dados_filtrados[[x[4] != 'FI70D' or x[5] > 2017 for x in dados_filtrados.values]]
dados_filtrados = dados_filtrados[[x[4] != 'FI70A' or x[5] > 2017 for x in dados_filtrados.values]]
dados_filtrados = dados_filtrados[[x[4] != 'GE70F' or x[5] > 2017 for x in dados_filtrados.values]]
#dados_filtrados

In [274]:
from collections import Counter

disciplinas_comunidades = []

# Pega as disciplinas de cada comunidade
for idx, comunidade in enumerate(comunidades):
    disciplinas_comunidades.append(pd.DataFrame())
    for id in comunidade:
        disciplinas_comunidades[idx] = pd.concat([disciplinas_comunidades[idx],
                   dados_filtrados[dados_filtrados.ID_ANONIMO.apply(lambda a: a == int(id))]
                  ])
        pass

# Pega as disciplinas mais populares em cada comunidade
for idx, comunidade in enumerate(disciplinas_comunidades):
    print("Comunidade " + str(idx) + ": " + str(Counter(comunidade.CODIGO).most_common(8)))

Comunidade 0: [('CSH30', 55), ('MA70C', 25), ('FI70D', 19), ('CSH42', 18), ('FI70A', 17), ('FI70B', 13), ('EL64B', 11), ('ES70B', 11)]
Comunidade 1: [('CSV30', 64), ('CSH30', 31), ('CSV40', 24), ('CSA41', 21), ('CSI53', 15), ('CSR44', 13), ('CSB41', 13), ('CSV45', 12)]
Comunidade 2: [('CSH30', 53), ('CSM40', 16), ('CSH42', 15), ('CSR41', 12), ('CSR43', 10), ('CSM43', 9), ('ES70N', 8), ('CSH44', 8)]
